## Vibrational Energy & Wavefunctions
<br>
Given a diatomic potential computed by some means, such as through Hartree-Fock or RKR, it is possible to use a basis of linearly independent functions to compute the vibrational energy levels of the molecule, as well as compute the actual wavefunctions themselves that govern the moleceule per quantum physics.
<br><br>
In this notebook, the RKR method will be used to generate the potential for $\text{CO}$. Once the potential is fitted and created, an Extended Rydberg Potential is fitted to the RKR potential that allows for a continous function to represent the potential.
<br><br>
The Schrödinger equation of the form $\hat{H}\Psi = E\Psi$ is used for this calculation. The wavefunction $\Psi$ will be represented by a linear combination of basis functions from the basis set, which in this case will be Harmonic Oscillators represented by $\psi_i$. The above equation can be represented as an eigen value problem where the vibrational energy levels are repersented by $E$, the eigen values. $\hat{H}$ represents the Hamiltonian operator, which when acts upon the wavefunction and returns the energy, $E$. 
$$\hat{H} = \hat{V} + \hat{T}$$
The potential energy $V(r)$ is defined as:
$$V(r) = \int_0^{\infty}{\psi_iR(r)\psi_j dr}$$
Where $R(r)$ is the potential energy surface represented through the Extended Rydberg Potential.
The kinetic energy $T(r)$ is represented as:
$$T(r) = \int_0^{\infty}{\psi_i\frac{-\hbar^2}{2m}\frac{\partial^2}{\partial r^2}\psi_j dr}$$
As can be seen, two diffrent basis functions are used for the equations for $V(r)$ and $T(r)$. This is because the basis set is of some set integer size, for example, 10 or 22, and each the equations for $T$ and $V$ are evaluated for each possible combination of basis functions. This results in $H$ being a square matrix the same size as the basis.
<br><br>
Once $\hat{H}$ has been computed, the eigen values of the hamiltonian are computed which are then the vibrational energy states of the system and graphed alongside the potential energy curve. 
<br><br>
The overall steps for this procedure are listed here: 
<ol>
  <li>Input Diatomic Potential Data.</li>
  <li>If needed, fit the data to a potential function, such as the Extended Rydberg Potential</li>
  <li>Choose a basis set and a size to represent $\Psi$</li>
  <li>Compute the $T(r)$ Matrix</li>
  <li>Compute the $V(r)$ Matrix</li>
  <li>Add $T$ and $V$ to compute $\hat{H}$</li>
  <li>Compute the eigen system for $\hat{H}$, where the eigen values are the vibrational energy levels for the molecule and the the eigen vectors the wavefunction coefficients.
</ol>
This notebook uses wavenumbers for energy, angstroms for distance, and atomic units for mass.
All information in this notebook orginates from the following <a href="http://hyperphysics.phy-astr.gsu.edu/hbase/quantum/hamil.html">website</a>, and from the <i>Franck-Condon Calculations</i> and <i>Diatomic Molecule</i> Matematica Notebooks provided by Dr. Jerry LaRue of Chapman University. 

In [1]:
import time
import numpy as np
from tqdm import tqdm
from scipy.integrate import quad as integrate
from scipy.misc import derivative as ddx
from scipy.linalg import eigh

#Set up Graphing Abillties with Plotly
from plotly.offline import iplot, init_notebook_mode
init_notebook_mode(connected=True)

figure = {
   "data":[],
   "layout":{
       "xaxis":{"title":"Bond Distance in Angstroms"},
       "yaxis":{"title":"Energy in Wavenumbers"}
   }
}

startTime = time.time()

In [2]:
#Step 1, Input the Diatomic Potential Data
#For the purposes of this notebook, the potential will be computed using RKR,
#but the use of Hartree-Fock, DFT or other theories will work as well
#The Diatomic Potential is for COX, and the diatomic constants are from the NIST Webbook
from RKRClass import RKR

rkr = RKR()

#RKR Values for CO
#rkr.setDiatomicConstants(0.01750441, 1.93128087, 2169.81358, 13.28831, 0, 0, 0)
#rkr.setReducedMass((12*16)/(12+16))

#RKR Values for H2
rkr.setDiatomicConstants(3.062, 60.8530, 4401.21, 121.33, 0, 0, 0)
rkr.setReducedMass(0.5)

x, y = rkr.graphData(resolution=.001, endPoint=16)

#Manually Add in Minimum Data point which is not computed by the RKR
#CO: 1.128323, H2: .74144
x.append(.74144)
y.append(0)


figure["data"].append(
    {
        "type":"scatter",
        "x":x,
        "y":y,
        "connectgaps":True,
        "mode":"markers",
        "name":"RKR Potential"
    }
)

print("Plotting Figure")
iplot(figure)


Generating RKR Potential


 63%|████████████████████████████████████████████████▎                            | 1034/1650 [00:03<00:02, 277.42it/s]

(0.43027073806140953, 2.039726638156258, 33040.291673070016)


100%|█████████████████████████████████████████████████████████████████████████████| 1650/1650 [00:05<00:00, 291.07it/s]


Plotting Figure


In [3]:
#Step 2, Fit the Data to a Potential Energy Functoin 
#In this case, the Extended Rydberg Potential will be used
from diatomicPotentials import extendedRydberg

R = extendedRydberg()

R.fitPotential(x, y)

#Should the Optimal Bond Distance point be zeroed?
R.zeroRe = True

xr, yr = R.graphData(1/5, 4)

figure["data"].append(
    {
        "x":xr,
        "y":yr,
        "name":"Extended Rydberg Fit"
    }
)

print("Plotting Figure")
iplot(figure)

A:\School\Chapman\Research\QM\CatLab_CompChem\Vibrational Energy & Wavefunctions\diatomicPotentials.py:48: RuntimeWarning:

overflow encountered in multiply



39584.78679224626
0.7387096443473156
3.5009773707200478
2.2940076656981003
2.7748698474227735
39583.786792318504
Plotting Figure


In [4]:
#Step 3, Select a Basis Set and Size
#For this notebook, the Harmonic Oscilator Basis Set is used
from BasisSets import HOW

basisSize = 10

#Build the Basis Set of size 5
basis = HOW(.74144, rkr.we, rkr.u, basisSize)
#H2: .74144 CO: 1.128323
x, y = basis.graphData()

for index, yData in enumerate(y):
    figure["data"].append(
        {
            "x":x, 
            "y":yData,
            "name":"HOW " + str(index)
        }
    )
    
iplot(figure)

Graphing Data


100%|███████████████████████████████████████████████████████████████████████████████| 500/500 [00:01<00:00, 490.13it/s]


## Unit Analysis 
<br>
Below are the unit analyses for the $T(r)$ and $V(r)$ integrals. Since $\hat{H} = T(r) + V(r)$, both $T(r)$ and $V(r)$ must be in the same units of energy, which for this calculation will be wavenumbers.
<br><br>
$$\begin{align}
    T(r) &= \int_0^{\infty}{\psi_i\frac{-\hbar^2}{2m}\frac{\partial^2}{\partial r^2}\psi_j dr} \\
        &= \left[\frac{1}{\sqrt{{\buildrel _{\circ} \over {\mathrm{A}}}}}
            \frac{\left(\frac{kg \cdot m^2}{s}\right)^2}{kg}
            \frac{\frac{1}{\sqrt{{\buildrel _{\circ} \over {\mathrm{A}}}}}}{{\buildrel _{\circ} \over {\mathrm{A}}}^2} 
        \right] 
        \cdot {\buildrel _{\circ} \over {\mathrm{A}}} \\
        &= \left[\frac{1}{\sqrt{{\buildrel _{\circ} \over {\mathrm{A}}}}}
            \frac{\frac{kg^2 \cdot m^4}{s^2}}{kg}
            \frac{1}{\sqrt{{\buildrel _{\circ} \over {\mathrm{A}}}}{\buildrel _{\circ} \over {\mathrm{A}}}^2} 
        \right] 
        \cdot {\buildrel _{\circ} \over {\mathrm{A}}} \\
        &= \left[\frac{1}{{\buildrel _{\circ} \over {\mathrm{A}}}}
            \frac{kg^2 \cdot m^4}{kg \cdot s^2}
            \frac{1}{{\buildrel _{\circ} \over {\mathrm{A}}}^2} 
        \right] 
        \cdot {\buildrel _{\circ} \over {\mathrm{A}}} \\
        &= \frac{1}{{\buildrel _{\circ} \over {\mathrm{A}}}}
            \frac{kg \cdot m^4}{s^2}
            \frac{1}{{\buildrel _{\circ} \over {\mathrm{A}}}}  
        \\
        &= \frac{1}{{\buildrel _{\circ} \over {\mathrm{A}}}^2}
            \frac{kg \cdot m^4}{s^2}  
        \\
         &= \frac{1}{m^2}
            \frac{kg \cdot m^4}{s^2} &&[\mbox{Convert Angstroms to Meters}] 
        \\
        &= \frac{kg \cdot m^2}{s^2} \\
        &= J &&[\mbox{Definitions of Joules}] \\
      T(r)  &= \frac{1}{cm} &&[\mbox{Convert Joules to Wavenumbers}]
\end{align}$$
<br><br>
$$\begin{align}
    V(r) &= \int_0^{\infty}{\psi_i R(r) \psi_j } \\
         &= \left[ \frac{1}{\sqrt{{\buildrel _{\circ} \over {\mathrm{A}}}}} \frac{1}{cm} \frac{1}{\sqrt{{\buildrel _{\circ} \over {\mathrm{A}}}}}\right] \cdot {\buildrel _{\circ} \over {\mathrm{A}}} \\
         &= \left[ \frac{1}{cm}\frac{1}{\sqrt{{\buildrel _{\circ} \over {\mathrm{A}}}}}\right] \cdot {\buildrel _{\circ} \over {\mathrm{A}}} \\
     V(r) &= \frac{1}{cm}
\end{align}$$

## Computational Note
<br><br>
Due to the use of both numerical derivation and integration in a combined fashion, $\int{\frac{d}{dx}f(x)dx}$, the integrals for the T(r) matrix are extremely slow to compute. As a pedagogical example of how numerical analysis and the subsequent programming is applied to these types of programs, the cell below makes use of numerical methods. 
<br><br>
Fortunately, in the case of the $T(r)$ matrix, there is an analytical method to compute $T$ which and is also implemented to demonstrate that although the speeds of the methods differ greatly, the results are identical.

In [5]:
'''#Step 4. Compute the T(r) Matrix
T = np.zeros([basis.size, basis.size])

#From Google
angstromToMeters2 = pow(10, -20)

#From "Introduction To Computational Physical Chemistry" by Joshua Schrier
joulesToWavenumbers = 5.034116 * pow(10, 22)

conversionFactor = joulesToWavenumbers / angstromToMeters2

c0 = -(basis.hbar ** 2) / (2 * basis.u)
print(c0 * conversionFactor)

#print("Computing T(v)")
#for index1 in tqdm(range(basis.size)):
#    b1 = basis.basis[index1]
#    for index2, b2 in enumerate(basis.basis):
        
#        integrand = lambda r : b1(r) * c0  * conversionFactor *  ddx(b2, r, dx=pow(10, -15))
#        T[index1, index2] += round(integrate(integrand, 0, np.inf, limit=200)[0], 10) 
        
#print(T)'''

'#Step 4. Compute the T(r) Matrix\nT = np.zeros([basis.size, basis.size])\n\n#From Google\nangstromToMeters2 = pow(10, -20)\n\n#From "Introduction To Computational Physical Chemistry" by Joshua Schrier\njoulesToWavenumbers = 5.034116 * pow(10, 22)\n\nconversionFactor = joulesToWavenumbers / angstromToMeters2\n\nc0 = -(basis.hbar ** 2) / (2 * basis.u)\nprint(c0 * conversionFactor)\n\n#print("Computing T(v)")\n#for index1 in tqdm(range(basis.size)):\n#    b1 = basis.basis[index1]\n#    for index2, b2 in enumerate(basis.basis):\n        \n#        integrand = lambda r : b1(r) * c0  * conversionFactor *  ddx(b2, r, dx=pow(10, -15))\n#        T[index1, index2] += round(integrate(integrand, 0, np.inf, limit=200)[0], 10) \n        \n#print(T)'

In [6]:
#Analytical Method for computing T

T2 = np.zeros([basis.size, basis.size])

for b1 in range(basis.size):
    for b2 in range(basis.size):
        
        if(b1 == b2):
            t = 2*b1 + 1
        elif(b1 == b2 + 2):
            t = -np.sqrt( b1 * (b1 - 1) )
        elif(b1 == b2 - 2):
            t = -np.sqrt( (b1+1) * (b1+2)  )
        else:
            t = 0
        T2[b1, b2] += round(t, 2)    

#Multiply by RKR Omega to have units of 1/cm
#Basis Omega has units of Hertz
#Should divison be by 4 or by 25
T2 *= rkr.we / 4

print(T2)

[[ 1100.3025       0.       -1551.426525     0.           0.
      0.           0.           0.           0.           0.      ]
 [    0.        3300.9075       0.       -2695.741125     0.
      0.           0.           0.           0.           0.      ]
 [-1551.426525     0.        5501.5125       0.       -3807.04665
      0.           0.           0.           0.           0.      ]
 [    0.       -2695.741125     0.        7702.1175       0.
  -4918.352175     0.           0.           0.           0.      ]
 [    0.           0.       -3807.04665      0.        9902.7225
      0.       -6029.6577       0.           0.           0.      ]
 [    0.           0.           0.       -4918.352175     0.
  12103.3275       0.       -7129.9602       0.           0.      ]
 [    0.           0.           0.           0.       -6029.6577
      0.       14303.9325       0.       -8230.2627       0.      ]
 [    0.           0.           0.           0.           0.
  -7129.9602       0.  

In [7]:
#Step 5. Compute the V(r) Matrix
#In order to improve speed of computation, only half the matrix is computed
#due to the the matrix being Hermitan and symettry existing across the diagnoal of the V

V = np.zeros([basis.size, basis.size])

print("Computing V(r)")
for index1 in tqdm(range(basis.size)):
    b1 = basis.basis[index1]
    for index2, b2 in enumerate(basis.basis):
        
        if(index1 > index2):
            V[index1, index2] = V[index2, index1]
            continue
        
        integrand = lambda r : b1(r) * R.equation(r) * b2(r)
        V[index1, index2] += integrate(integrand, 0, np.inf,  epsabs = pow(10, -500), limit = 200)[0]
        
print(V)

Computing V(r)


100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:19<00:00,  2.10s/it]


[[ 1.24444808e+03 -6.92961343e+02  1.91379792e+03 -6.72983713e+02
   1.86467635e+02 -4.53101766e+01  9.67416957e+00 -1.81908079e+00
   3.04358445e-01 -4.59009739e-02]
 [-6.92961343e+02  3.95096705e+03 -2.14563731e+03  3.68773050e+03
  -1.44728406e+03  4.40651088e+02 -1.15799648e+02  2.64563025e+01
  -5.28284036e+00  9.33037258e-01]
 [ 1.91379792e+03 -2.14563731e+03  7.11423659e+03 -4.19875570e+03
   5.78011651e+03 -2.45688877e+03  8.05884611e+02 -2.25920701e+02
   5.46766620e+01 -1.15045610e+01]
 [-6.72983713e+02  3.68773050e+03 -4.19875570e+03  1.07775209e+04
  -6.83843274e+03  8.24200116e+03 -3.72511497e+03  1.29869421e+03
  -3.84540023e+02  9.78325401e+01]
 [ 1.86467635e+02 -1.44728406e+03  5.78011651e+03 -6.83843274e+03
   1.49866306e+04 -1.00801876e+04  1.11144431e+04 -5.27603256e+03
   1.93602840e+03 -6.00933519e+02]
 [-4.53101766e+01  4.40651088e+02 -2.45688877e+03  8.24200116e+03
  -1.00801876e+04  1.97900230e+04 -1.39531341e+04  1.44381027e+04
  -7.13600582e+03  2.73587350e+03

In [8]:
#Step 6. Compute H

H =  V + T2

#print(H)

In [9]:
#Step 7. Compute the Eigen System for H
ev, evc = eigh(H)
evc = evc.transpose()

figure["data"].append(
   {
        "type":"scatter",
        "x":[1.3] * len(ev),
        "y":[float(e) for e in ev],
        "connectgaps":False,
        "mode":"markers",
        "name":"Vibrational Energy Levels"
    }
)

iplot(figure)

In [10]:
def waveFunction(r, v, evec, basisFunctions):
    answer = 0
    
    for index, basis in enumerate(basisFunctions):
        answer += evc[v, index] * basis(r)
    
    return float(answer)

x = np.arange(0, 3, .01)
for i in tqdm(range(len(basis.basis))):
    y = [ waveFunction(r, i, evc, basis.basis) for r in x  ]

    figure["data"].append(
        {
            "x":x,
            "y":y,
            "name":str(i)
        }
    )
    
iplot(figure)

100%|██████████████████████████████████████████████████████████████████████████████████| 10/10 [00:07<00:00,  1.37it/s]


In [11]:
#Wavefunction Energy Accuracy Computation

print("Computation Accuracy\n")

accuracy = []
for v, energy in enumerate(ev):
    accuracy.append ( abs(rkr.E(v)-energy) / rkr.E(v) * 100)
    print("v=" + str(v) + ": " + str(accuracy[-1]) + "% Inaccurate")
    
print("\nOverall Error: " + str( sum(accuracy)/len(accuracy) ) + "%")
print()

print("Total Execution Time: " + str(time.time() - startTime) + " Seconds")

Computation Accuracy

v=0: 2.648484119606011% Inaccurate
v=1: 1.7768352237308833% Inaccurate
v=2: 1.2935763496617663% Inaccurate
v=3: 1.8209549116673371% Inaccurate
v=4: 5.250761238572233% Inaccurate
v=5: 13.570978587007222% Inaccurate
v=6: 23.147758530182845% Inaccurate
v=7: 38.690065307737456% Inaccurate
v=8: 95.55404155914358% Inaccurate
v=9: 265.4346419526493% Inaccurate

Overall Error: 44.91880977799586%

Total Execution Time: 36.41915249824524 Seconds
